In [1]:
import os
import h5py
import pandas as pd
import numpy as np
import seaborn as sns

In [2]:
import matplotlib as mpl
import matplotlib.pyplot as plt
# PLOTTING OPTIONS
fig_width_pt = 3*246.0  # Get this from LaTeX using \showthe\columnwidth
inches_per_pt = 1.0/72.27               # Convert pt to inch
golden_mean = (np.sqrt(5)-1.0)/2.0         # Aesthetic ratio
fig_width = fig_width_pt*inches_per_pt  # width in inches
fig_height = fig_width*golden_mean      # height in inches
fig_size =  [fig_width,fig_height]

params = { 'axes.labelsize': 24,
          'font.family': 'serif',
          'font.serif': 'Computer Modern Raman',
          'font.size': 24,
          'legend.fontsize': 20,
          'xtick.labelsize': 24,
          'ytick.labelsize': 24,
          'axes.grid' : True,
          'text.usetex': True,
          'savefig.dpi' : 100,
          'lines.markersize' : 14,
          'figure.figsize': fig_size}

mpl.rcParams.update(params)

from pycbc import conversions
from pycbc import detector

In [3]:
d221 = pd.read_csv('./reproduce/t6/221/GW150914_PROD1_Kerr_221_0M/Nested_sampler/posterior.dat',sep=' ')
d221.columns = [d221.columns[(i+1)%len(d221.columns)] for i in range(len(d221.columns))]
d221.drop(columns='#',inplace=True)

In [4]:
d221

Mf        af     A2220     A2221   phi2220   phi2221  \
0       72.444419  0.685669  5.485424  0.261236  5.577737  0.139087   
1       60.647343  0.224913  4.417553  2.726996  6.172681  4.279614   
2      109.942012  0.960884  0.814147  4.859725  4.613551  0.036135   
3       67.756361  0.608115  8.708519  7.552168  5.647384  2.226254   
4      112.875408  0.947589  0.221065  4.562956  0.952363  0.129043   
...           ...       ...       ...       ...       ...       ...   
10781   76.488394  0.784670  5.762782  7.074695  5.185695  1.498296   
10782   74.876464  0.766137  5.855266  6.963844  5.223199  1.538106   
10783   71.128600  0.690774  6.751077  8.834128  5.303243  1.699820   
10784   73.512088  0.734402  6.287531  7.713808  5.297240  1.680110   
10785   74.964282  0.769391  5.889901  7.152684  5.197893  1.537970   

               logL  logPrior  
0      38762.350241       0.0  
1      38765.117169       0.0  
2      38765.247884       0.0  
3      38765.968626       0.0  
4      38766.021826       0.0  
...             ...       ...  
10781  38778.965480       0.0  
10782  38778.985092       0.0  
10783  38778.992359       0.0  
10784  38779.004591       0.0  
10785  38779.016128       0.0  

[10786 rows x 8 columns]

In [5]:
d221['logL'].values[-1]

38779.01612841951

In [6]:
conversions.snr_from_loglr(d221['logL'].values[-1] - 38724.013136349546)

10.488373760499494

# Time

In [8]:
ra = 1.95
dec = -1.27
psi = 0.82
th1 = 1126259462.423235

In [9]:
det = detector.Detector('H1')

In [10]:
delay = det.time_delay_from_earth_center(ra,dec,th1)
print(delay)

0.01468531251688538


In [11]:
tc = th1 - delay

In [12]:
print(tc)

1126259462.4085495


In [13]:
tc + det.time_delay_from_earth_center(ra,dec,tc) - th1

0.0

# Read in PyCBC GW150914 config.ini

In [14]:
from pycbc.inference import io, models
from pycbc.workflow import WorkflowConfigParser

In [15]:
cp = WorkflowConfigParser(['./inference-GW150914_095045.ini'])

In [1]:
cp.set('static_params','harmonics','spherical')

NameError: name 'cp' is not defined

In [30]:
params = {'final_mass':d221['Mf'].values[-1],
         'final_spin':d221['af'].values[-1],
         'amp220':d221['A2220'].values[-1]*1e-21,
         'phi220':d221['phi2220'].values[-1],
         'amp221':d221['A2221'].values[-1]/d221['A2220'].values[-1],
         'phi221':d221['phi2221'].values[-1]}

In [46]:
cp.set('static_params','harmonics','spherical')

In [47]:
model = models.read_from_config(cp)

In [48]:
model.update(**params)

In [49]:
model.current_params

{'final_mass': 74.9642816665504,
 'final_spin': 0.7693909269973396,
 'amp220': 5.889900875719935e-21,
 'phi220': 5.197892748005424,
 'amp221': 1.2143980843851219,
 'phi221': 1.5379702539900164,
 'approximant': 'TdQNMfromFinalMassSpin',
 'harmonics': 'spherical',
 'tref': 1126259462.4085495,
 'ra': 1.95,
 'dec': -1.27,
 'toffset': 0.0,
 'lmns': 222.0,
 'polarization': 0.82,
 'inclination': 3.1415926}

In [50]:
model.loglikelihood

-619050.6335457675

In [51]:
# get the matched-filter SNR
print((2*model.loglr)**0.5)

7.4494654768093955


## Documenting some results

PyCBC SNR:

spheroidal: 7.046724536677377

spherical: 7.4494654768093955

# PyCBC results

In [52]:
# load the posterior file
fp = io.loadfile('extract.hdf', 'r')
# get the config, the data, and PSDs from the file
# the config file:
cp = fp.read_config_file()
# the data
data = fp.read_data()
# the psds
psds = fp.read_psds()

In [53]:
# now let's load the model
model = models.read_from_config(cp, data=data, psds=psds)

In [54]:
# let's get the maximum likelihood point
samples = fp.read_samples(list(fp['samples'].keys()))
maxlidx = samples['loglikelihood'].argmax()
maxlparams = {p: samples[p][maxlidx] for p in model.variable_params}

In [57]:
# get the loglikelihood of these points
model.update(**maxlparams)
model.loglikelihood

-618992.8520172711

In [64]:
maxlparams

{'final_mass': 71.48874281792715,
 'final_spin': 0.7154564522032227,
 'amp220': 6.599426050915941e-21,
 'phi220': 4.252001686582448,
 'absamp221': 1.1309311226882227e-20,
 'phi221': 0.8281597614507725}

In [58]:
# get the matched-filter SNR
print((2*model.loglr)**0.5)

13.078897504324436


In [61]:
params = {'final_mass':d221['Mf'].values[-1],
         'final_spin':d221['af'].values[-1],
         'amp220':d221['A2220'].values[-1]*1e-21,
         'phi220':d221['phi2220'].values[-1],
         'absamp221':d221['A2221'].values[-1]*1e-21,
         'phi221':d221['phi2221'].values[-1]}

In [62]:
model.update(**params)
model.loglikelihood

-619053.5528077584

In [63]:
# get the matched-filter SNR
print((2*model.loglr)**0.5)

7.0466998626258714


# Plot posteriors